In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/trexquant/train.py
/kaggle/input/trexquant/env.py
/kaggle/input/trexquant/words_250000_train.txt
/kaggle/input/trexquant/hangman_api_user.ipynb
/kaggle/input/trexquant/network.py
/kaggle/input/trexquant/policy.h5
/kaggle/input/trexquant/utils.py
/kaggle/input/trexquant/demo.ipynb
/kaggle/input/cookies-txt/cookies.txt


In [2]:

from distutils.dir_util import copy_tree
copy_tree("/kaggle/input/trexquant","/kaggle/working")

['/kaggle/working/train.py',
 '/kaggle/working/env.py',
 '/kaggle/working/words_250000_train.txt',
 '/kaggle/working/hangman_api_user.ipynb',
 '/kaggle/working/network.py',
 '/kaggle/working/policy.h5',
 '/kaggle/working/utils.py',
 '/kaggle/working/demo.ipynb']

In [3]:
%%writefile network.py
import os

import numpy as np

from keras.layers import LSTM, Embedding, Input, Dense, GlobalAveragePooling1D, Concatenate,Bidirectional
from keras.models import Model
from keras import optimizers, backend as K

from warnings import filterwarnings

filterwarnings('ignore')
import random
from utils import letter_dict, letters, pad_sequences

class Network(object) :
    """Define the network
    network consists of two input that reads the current state 
    and one hot encoded matrix of guessed letters
    This class includes some helper function to ease training and inference
    """
    def __init__(self, maxlen = 29) :
        state_embedding = self.get_state_embedding(maxlen)
        guessed_embedding = self.get_guessed_embedding()
        x = Concatenate()([state_embedding.output, guessed_embedding.output])
        x = Dense(100, activation = 'tanh')(x)
        x = Dense(26, activation = 'softmax')(x)
        self.full_model = Model([state_embedding.input, guessed_embedding.input], x, name = 'fullmodel')
        self.compile()
        
    def get_state_embedding(self, maxlen = 29) :
        inp = Input(shape = (maxlen,))
        x = Embedding(30,100, mask_zero = True)(inp)
        x = Bidirectional(LSTM(100 , dropout = 0.2, return_sequences=True))(x)
        x = Bidirectional(LSTM(100, dropout = 0.2 , return_sequences=True))(x)
        x = GlobalAveragePooling1D()(x)
        x = Dense(100, activation = 'tanh')(x)
        return Model(inp,x , name = 'StateEmbedding')
    
    def get_guessed_embedding(self) :
        inp = Input(shape = (26,))
        x = Dense(60, activation = 'tanh')(inp)
        x = Dense(60, activation = 'tanh')(x)
        return Model(inp, x, name = 'GuessedEmbedding')

    def __call__(self, state, guessed) :
        return self.full_model.predict([state,guessed]).flatten()
    
    def fit(self, *args, **kwargs) :
        return self.full_model.fit(*args, **kwargs)
    
    def train_on_batch(self, *args, **kwargs) :
        return self.full_model.train_on_batch(*args, **kwargs)        
    
    def summary(self) :
        self.full_model.summary()

    def save(self, *args, **kwargs) :
        self.full_model.save(*args, **kwargs)

    def load_weights(self, *args, **kwargs) :
        self.full_model.load_weights(*args, **kwargs)
        self.compile()

    def compile(self, optimizer= None) : 
        if optimizer is not None :
            self.full_model.compile(loss = 'categorical_crossentropy', optimizer = optimizer)
        else :
            self.full_model.compile(loss = 'categorical_crossentropy', optimizer = optimizers.Adam(1e-3, clipnorm=1))

class Agent(object) :

    """Agent definition.
    Agent is embedded with a model and policy
    Agent can use stochastic policy i.e. choose action randomly from computed probability 
    or greedy i.e choose the most probable action out of unused actions.
    
    Agent is trained off-policy, after a set amount of episode (in my case I trained with 3 episodes), 
    and after each episode during training must be finalized with finalize_episode method 
    to compute the correct course of actions.

    train_model method will collect accumulated episodes and perform one iteration of gradient descent
    with the collected episode data.

    Tried both with stochastic and greedy. Greedy policy performs converges better.
    """

    def __init__(self, model, policy = 'greedy') :
        self.reset_guessed()
        if policy not in ['stochastic', 'greedy'] :
            raise ValueError('Policy can only be stochastic or greedy')
        self._policy = 'greedy'
        self.policy = property(self.get_policy, self.set_policy)
        self.reset_guessed()
        self.is_training = True
        self.model = model

    @staticmethod
    def guessed_mat(guessed) :
        mat = np.empty([1,26])
        for i, l in enumerate(letters) :
            mat[0,i] = 1 if l in guessed else 0
        return mat
    
    def get_guessed_mat(self) :
        return self.guessed_mat(self.guessed)

    def reset_guessed(self) :
        self.guessed = []

    def get_probs(self, state) :
        raise NotImplementedError()

    def get_policy(self) :
        return self._policy

    def set_policy(self, policy) :
        if policy not in ['stochastic', 'greedy'] :
            raise ValueError('Policy can only be stochastic or greedy')
        self._policy = policy

    def select_action(self,state) :            
        probs = self.get_probs(state)
        if self._policy == 'greedy' :
            i = 1
            sorted_probs = probs.argsort()
            while letters[sorted_probs[-i]] in self.guessed :
                i+= 1
            idx_act = sorted_probs[-i]
        elif self._policy == 'stochastic' :
            idx_act = np.random.choice(np.arange(probs.shape[0]), p = probs)
        guess = letters[idx_act]
        if guess not in self.guessed :
            self.guessed.append(guess)
            
        return guess
        
    def eval(self) :
        self.is_training = False
        self.set_policy('greedy') 
    
    def train(self) :
        self.is_training = True

class NNAgent(Agent) :
    def __init__(self, model, maxlen=29, policy='greedy') :
        super().__init__(model, policy)
        self.episode_memory = []
        self.states_history = []
        self.maxlen = maxlen

    def train_model(self):
        inp_1, inp_2, obj = zip(*self.states_history)
        inp_1 = np.vstack(list(inp_1)).astype(float)
        inp_2 = np.vstack(list(inp_2)).astype(float)
        obj = np.vstack(list(obj)).astype(float)
        loss = self.model.train_on_batch([inp_1,inp_2], obj)
        self.states_history = []
        return loss

    def get_probs(self, state) :
        state = self.preprocess_input(state)
        probs = self.model(*state)
        probs /= probs.sum()
        return probs

    def finalize_episode(self, answer) :
        inp_1, inp_2 = zip(*self.episode_memory)
        inp_1 = np.vstack(list(inp_1)).astype(float)      #stack the game state matrix
        inp_2 = np.vstack(list(inp_2)).astype(float)      #stack the one hot-encoded guessed matrix
        obj = 1.0 - inp_2                                 #compute the unused letters one-hot encoded
        len_ep = len(self.episode_memory)                 #length of episode
        correct_mask = np.array([[1 if l in answer else 0 for l in letters]]) # get mask from correct answer
        correct_mask = np.repeat(correct_mask, len_ep, axis = 0).astype(float)
        obj = correct_mask * obj  #the correct action is choosing the letters that are both unused AND exist in the word
        obj /= obj.sum(axis = 1).reshape(-1,1) #normalize so it sums to one
        self.states_history.append((inp_1, inp_2,obj))
        self.episode_memory = []
        self.reset_guessed()
    
    def preprocess_input(self, state) :
        new_input = []
        for l in state :
            new_input.append(letter_dict[l])
        state = pad_sequences([new_input], maxlen = self.maxlen)
        if self.is_training :
            self.episode_memory.append((state,self.get_guessed_mat()))
        return state, self.get_guessed_mat()



if __name__ =='__main__' :
    pass

Overwriting network.py


In [4]:
%%writefile train.py
import os

from tqdm import tqdm

from env import Hangman
from network import Network, NNAgent
from utils import *
from keras import optimizers

import numpy as np

with open('words_250000_train.txt') as f :
    word_src = f.read().splitlines()

len_list = list(map(len, word_src))
maxlen = max(len_list)
print('Max length of words is', maxlen) 

policy_net = Network(maxlen=maxlen)
player = NNAgent(policy_net)
policy_net.summary()


save_episode = 100
view_episode = 100
update_episode = 5
avg_correct = 0
wins_avg = 0
n_trials = 200
progbar = tqdm(range(n_trials))

""" 
Warmup Phase
Since the network can only collect data by interacting with the environment, 
to collect more data max_lives parameter or the maximum number of trial before game over is set 
slightly extra than the actual game parameter so episodes are longer. 
"""

game_params = {'max_lives' : 6}
env = Hangman(word_src, **game_params)


for episode_set in progbar :
    for _ in range(update_episode) :
        state = env.reset()
        done = False
        correct_count = 0
        while not done :
            guess = player.select_action(state)
            state, reward, done, ans,_ = env.step(guess)
            if reward > 0 :
                correct_count += 1.0
            if reward == env.win_reward :
                wins_avg += 1.0
        player.finalize_episode(ans['ans'])
        avg_correct += correct_count
    loss = player.train_model()
    progbar.set_description("Loss : {:.3f}              ".format(loss))

    if (episode_set +1) % view_episode == 0 :
        views = (episode_set + 1,avg_correct/(update_episode*view_episode), view_episode*update_episode, wins_avg/(update_episode*view_episode))
        print('Episode {} -------- Average Correct Count : {:.3f}     Last {} winrate : {:.3f}'.format(*views))
        if loss is not None :
            print('Loss :', loss)
            print()
            avg_correct = 0
            wins_avg = 0

    if (episode_set +1) % save_episode == 0 :
        player.model.save('policy.h5', include_optimizer=False)

print()
game_params = {'max_lives' : 6}
env = Hangman(word_src, **game_params)

""" 
Final Phase, 
Collect data by interacting with similar parameter as the actual game.
"""

n_trials = 300
progbar = tqdm(range(n_trials))

player.model.compile(optimizer= optimizers.Adam(2e-2, clipnorm=1))

for episode_set in progbar :
    for _ in range(update_episode) :
        total_reward = 0    
        state = env.reset()
        done = False
        correct_count = 0
        while not done :
            guess = player.select_action(state)
            state, reward, done, ans,_ = env.step(guess)
            #player.append_sample(letter_dict[guess] - 1, reward)
            if reward > 0 :
                correct_count += 1.0
            if reward == env.win_reward :
                wins_avg += 1.0
        player.finalize_episode(ans['ans'])
        avg_correct += correct_count
    loss = player.train_model()
    progbar.set_description("Loss : {:.3f}              ".format(loss))

    if (episode_set +1) % view_episode == 0 :
        views = (episode_set + 1,avg_correct/(update_episode*view_episode), view_episode, wins_avg/(update_episode*view_episode))
        print('Episode {} -------- Average Correct Count : {:.3f}     Last {} winrate : {:.3f}'.format(*views))
        if loss is not None :
            print('Loss :', loss)
            print()
            avg_correct = 0
            wins_avg = 0

    if (episode_set +1) % save_episode == 0 :
        player.model.save('policy.h5', include_optimizer=False)

Overwriting train.py


In [5]:
%run train.py

Max length of words is 29


Model: "fullmodel"

┏━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)        ┃ Output Shape      ┃    Param # ┃ Connected to      ┃
┡━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━┩
│ input_layer         │ (None, 29)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ embedding           │ (None, 29, 100)   │      3,000 │ input_layer[0][0] │
│ (Embedding)         │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ not_equal           │ (None, 29)        │          0 │ input_layer[0][0] │
│ (NotEqual)          │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ bidirectional       │ (None, 29, 200)   │    160,800 │ embedding[0][0],  │
│ (Bidirectional)     │                   │            │ not_equal[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ bidirectional_1     │ (None, 29, 200)   │    240,800 │ bidirectional[0]… │
│ (Bidirectional)     │                   │            │ not_equal[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ input_layer_1       │ (None, 26)        │          0 │ -                 │
│ (InputLayer)        │                   │            │                   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ global_average_poo… │ (None, 200)       │          0 │ bidirectional_1[… │
│ (GlobalAveragePool… │                   │            │ not_equal[0][0]   │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_1 (Dense)     │ (None, 60)        │      1,620 │ input_layer_1[0]… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense (Dense)       │ (None, 100)       │     20,100 │ global_average_p… │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_2 (Dense)     │ (None, 60)        │      3,660 │ dense_1[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ concatenate         │ (None, 160)       │          0 │ dense[0][0],      │
│ (Concatenate)       │                   │            │ dense_2[0][0]     │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_3 (Dense)     │ (None, 100)       │     16,100 │ concatenate[0][0] │
├─────────────────────┼───────────────────┼────────────┼───────────────────┤
│ dense_4 (Dense)     │ (None, 26)        │      2,626 │ dense_3[0][0]     │
└─────────────────────┴───────────────────┴────────────┴───────────────────┘

 Total params: 448,706 (1.71 MB)

 Trainable params: 448,706 (1.71 MB)

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 53ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━

Loss : 3.505              : 100%|█████████▉| 299/300 [42:29<00:07,  7.98s/it]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 59ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 63ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━

Loss : 3.504              : 100%|██████████| 300/300 [42:37<00:00,  8.53s/it]

Episode 300 -------- Average Correct Count : 4.304     Last 100 winrate : 0.050
Loss : 3.5044258

